In [1]:
#Mapping of Points Colored by Speed
import pandas as pd
import geopandas as gpd
import plotly.express as px
from pyproj import Transformer
from shapely import wkt
import plotly.graph_objects as go
import numpy as np

file_paths = [
    #'new_cleaned/cleaned_november.parquet'
    #'new_cleaned/cleaned_october.parquet',
    #'new_cleaned/cleaned_december.parquet',
    #'new_cleaned/cleaned_january.parquet',
    #'new_cleaned/cleaned_february.parquet',
    #'new_cleaned/cleaned_march.parquet',
    'new_cleaned/cleaned_april.parquet'
    # Add paths for all the months you have
]

# Load all runs data into a single GeoDataFrame
runs_list = [gpd.read_parquet(file_path) for file_path in file_paths]
runs = pd.concat(runs_list, ignore_index=True)

# Reset index to ensure clean, sequential indices before processing
runs.reset_index(drop=True, inplace=True)

# Calculate the total number of unique runs in the GeoDataFrame
total_runs = runs['run'].nunique()

print(f'Total number of unique runs: {total_runs}')

# Convert utcTime to datetime
runs['utcTime'] = pd.to_datetime(runs['utcTime'])

# Check and convert geometry column if necessary
if isinstance(runs['geometry'].iloc[0], str):
    runs['geometry'] = runs['geometry'].apply(wkt.loads)

# Define a transformer from UTM Zone 32N to WGS 84 (latitude and longitude)
transformer = Transformer.from_crs("epsg:32632", "epsg:4326", always_xy=True)

# Apply transformation to convert coordinates
runs['longitude'], runs['latitude'] = transformer.transform(runs['geometry'].x, runs['geometry'].y)





# Add jitter to the coordinates
jitter_strength = 0.0003  # Adjust the strength of the jitter as needed
runs['longitude_jitter'] = runs['longitude'] + np.random.uniform(-jitter_strength, jitter_strength, size=len(runs))
runs['latitude_jitter'] = runs['latitude'] + np.random.uniform(-jitter_strength, jitter_strength, size=len(runs))

# Plot all points with colors depending on speed
fig_map = px.scatter_mapbox(
    runs,
    lat='latitude_jitter',
    lon='longitude_jitter',
    color='speed',
    color_continuous_scale=px.colors.sequential.Viridis,  # Use the Viridis color scale
    size_max=10,
    zoom=10,
    mapbox_style='open-street-map',
    title='Map of Points Colored by Speed'
)

fig_map.show()


Total number of unique runs: 1400


In [ ]:
import pandas as pd
import geopandas as gpd


file_paths = [
    'new_cleaned/cleaned_november.parquet',
    'new_cleaned/cleaned_october.parquet',
    'new_cleaned/cleaned_december.parquet',
    'new_cleaned/cleaned_january.parquet',
    'new_cleaned/cleaned_february.parquet',
    'new_cleaned/cleaned_march.parquet',
    'new_cleaned/cleaned_april.parquet'
    # Add paths for all the months you have
]

# Load all runs data into a single GeoDataFrame
runs_list = [gpd.read_parquet(file_path) for file_path in file_paths]
runs = pd.concat(runs_list, ignore_index=True)

# Reset index to ensure clean, sequential indices before processing
runs.reset_index(drop=True, inplace=True)

# Calculate the total number of unique runs in the GeoDataFrame
total_runs = runs['run'].nunique()

print(f'Total number of unique runs: {total_runs}')

# Function to count stops
def count_stops(speed_series, stop_threshold=0):
    stops = 0
    stop_count = 0
    for speed in speed_series:
        if speed <= stop_threshold:
            stop_count += 1
        else:
            if stop_count > 0:
                stops += 1
                stop_count = 0
    return stops

# Calculate stops per run
run_stop_counts = runs.groupby('run')['speed'].apply(lambda x: count_stops(x))

# Calculate percentages
total_runs = len(run_stop_counts)
stops_1 = (run_stop_counts == 1).sum() / total_runs * 100
stops_2 = (run_stop_counts == 2).sum() / total_runs * 100

print(f"Percentage of runs with 1 stop: {stops_1:.2f}%")
print(f"Percentage of runs with 2 stops: {stops_2:.2f}%")